In [2]:
from evolution_operators import *
from utility_functions import *

In [63]:
def evaluate_strategy(data, fast_period, slow_period, fast_p_exit, slow_p_exit, stop_loss_percentage):
    # Calculate indicators
    print(fast_period,slow_period,fast_p_exit, slow_p_exit, stop_loss_percentage)
    data['MACD'], data['Signal'] = calculate_macd(data, fast_period, slow_period)
    data['MACD_E'], data['Signal_E'] = calculate_macd(data, fast_p_exit, slow_p_exit)

    data['ROC'] = calculate_roc(data, 3)
#     data['RSI_Derivative'] = calculate_rsi_derivative(data, rsi_period)
    
    # Apply trailing stop-loss exit condition
#     stop_loss = trailing_stop_loss(data, stop_loss_percentage)
    
    # Simulated trading logic
    position = 0  # 0 for no position, 1 for long position
    profit = 0
    total_trades = 0
    winning_trades = 0
    stricly_winning_trades =0
    
    stop_loss_price = 0
    
    for i in range(1, len(data)):
        try:

            if position == 0:
                if data['MACD'][i] > data['Signal'][i] :#and data['ROC'][i] > 1: #and data['RSI_Derivative'][i] > rsi_derivative_threshold:
                
                    position = 1  # Buy (enter long position)
                    entry_price = data['Close'][i]
                    stop_loss_price = entry_price - (entry_price * 0.01 * stop_loss_percentage)
                    print(f"Entry: {entry_price} on {data.index[i]} Stop Loss: {stop_loss_price}")
                    total_trades += 1
                    
            elif position == 1 and data['MACD'][i] < data['Signal'][i]:
                
                if data['Close'][i] > entry_price:  # Adjust stop loss only when the price goes up
                    stop_loss_price = max(stop_loss_price, data['Close'][i] - (data['Close'][i] * 0.01 * stop_loss_percentage))

                if data['Low'][i] < stop_loss_price:
                    position = 0  # Sell due to stop loss
                    exit_price = data['Open'][i] if stop_loss_price > data['Open'][i] else stop_loss_price
                    profit += exit_price - entry_price  # Calculate profit/loss
                    print(f"Exit: {exit_price} on {data.index[i]} exited on stop loss")
                    print(f"Profit: {profit}")
                    if(exit_price>= entry_price):
                        winning_trades += 1
                    if(exit_price> entry_price):
                        stricly_winning_trades += 1
                elif data['MACD_E'][i] < data['Signal_E'][i]:
                    position = 0  # Sell due to exit condition
                    exit_price = data['Close'][i]
                    profit += exit_price - entry_price  # Calculate profit/loss
                    print(f"Exit: {exit_price} on {data.index[i]} exited on MACD condition")
                    print(f"Profit: {profit}")
                    if(exit_price>= entry_price):
                        winning_trades += 1
                    if(exit_price> entry_price):
                        stricly_winning_trades += 1
        except:
            print("Something caused the error")
        win_rate = winning_trades/total_trades if total_trades != 0 else 0
    
    return [profit,total_trades,winning_trades,stricly_winning_trades,win_rate]

In [106]:
# Fetch historical stock data
ticker_symbol = 'adanient.NS'  # Replace with your desired stock symbol
start_date = '2022-01-01'
end_date = '2022-12-31'
stock_data = fetch_stock_data(ticker_symbol, start_date, end_date)

# Genetic Algorithm parameters
population_size = 200
num_generations = 20
mutation_rate = 0.1
elite_size = 30
consecutive_threshold = 3  # Number of consecutive generations with no fitness improvement to consider saturation
fitness_history = []  # To store fitness scores across generations

# GA: Initialization
def generate_individual():
    fast_p = random.randint(2,10)
    slow_p = random.randint(fast_p,20)
    fast_p_exit = random.randint(2,10)
    slow_p_exit = random.randint(fast_p_exit,20)
    return [fast_p,slow_p,fast_p_exit,slow_p_exit, random.uniform(-1,2)]


# Known or useful parameter values
known_parameters = [
#     [3, 4, 1, 10,0],
#     [7, 9, 5,9,  0],
#     [7, 9, 5,9,  3],
#     [2, 3, 2,4,  0],
#     [2, 15, 6, 10, 0],
    [2, 15, 3, 3, 3],
    [2, 18, 8, 14, -0.9930604812498026]# Example set of known parameters
                     # Add more known parameter sets if available
]

# Randomly generate the rest of the population
remaining_population = [generate_individual() for _ in range(population_size - len(known_parameters))]

# Initialize population using known parameter values and randomly generated values
population = known_parameters + remaining_population
# population = [generate_individual() for _ in range(population_size)]


    
for generation in range(num_generations):
    fitness_scores = [evaluate_strategy(stock_data.copy(), *individual)[0] for individual in population]
    sorted_population = [x for _, x in sorted(zip(fitness_scores, population), key=lambda pair: pair[0], reverse=True)]

    new_population = []

    # Select the top K individuals (elite) for the next generation
    elite = sorted_population[:elite_size]

    # Check for convergence or other stopping criteria
    fitness_history.append(max(fitness_scores))

    # Check for convergence or other stopping criteria
    if len(fitness_history) >= consecutive_threshold:
        recent_improvements = fitness_history[-consecutive_threshold:]
        if len(set(recent_improvements)) == 1:
            print("Saturation condition met, breaking the loop")
            break

    # Create new population by generating offspring from the elite individuals
    new_population = generate_offspring(elite,population_size,mutation_rate)

    population = new_population
    

# Find the best individual (parameters) from the final population
best_individual_index = np.argmax(fitness_scores)
best_individual = population[best_individual_index]
best_fitness_score = fitness_scores[best_individual_index]

print("Best Parameters:", best_individual)
print("Best Fitness Score:", best_fitness_score)


[*********************100%%**********************]  1 of 1 completed
2 15 3 3 3
Entry: 1751.8499755859375 on 2022-02-03 00:00:00 Stop Loss: 1699.2944763183593
Exit: 1699.2944763183593 on 2022-02-08 00:00:00 exited on stop loss
Profit: -52.55549926757817
Entry: 1783.1500244140625 on 2022-02-09 00:00:00 Stop Loss: 1729.6555236816407
Exit: 1729.6555236816407 on 2022-02-14 00:00:00 exited on stop loss
Profit: -106.04999999999995
Entry: 1738.0999755859375 on 2022-02-16 00:00:00 Stop Loss: 1685.9569763183595
Exit: 1685.9569763183595 on 2022-02-21 00:00:00 exited on stop loss
Profit: -158.192999267578
Entry: 1641.800048828125 on 2022-03-02 00:00:00 Stop Loss: 1592.5460473632813
Exit: 1590.0 on 2022-03-07 00:00:00 exited on stop loss
Profit: -209.993048095703
Entry: 1656.550048828125 on 2022-03-09 00:00:00 Stop Loss: 1606.8535473632812
Exit: 2166.8345947265625 on 2022-04-18 00:00:00 exited on stop loss
Profit: 300.2914978027345
Entry: 2286.35009765625 on 2022-04-21 00:00:00 Stop Loss: 2217.759

Profit: 1794.1519333633237
Entry: 4060.199951171875 on 2022-12-13 00:00:00 Stop Loss: 4048.097433876932
Exit: 4048.097433876932 on 2022-12-15 00:00:00 exited on stop loss
Profit: 1782.0494160683807
Entry: 4075.300048828125 on 2022-12-19 00:00:00 Stop Loss: 4063.152521633365
Exit: 4063.152521633365 on 2022-12-21 00:00:00 exited on stop loss
Profit: 1769.9018888736205
Entry: 3769.64990234375 on 2022-12-27 00:00:00 Stop Loss: 3758.413447566239
7 16 5 9 -0.937748846503413
Entry: 1786.0999755859375 on 2022-02-10 00:00:00 Stop Loss: 1802.8491075043924
Exit: 1736.300048828125 on 2022-02-14 00:00:00 exited on stop loss
Profit: -49.7999267578125
Entry: 1656.550048828125 on 2022-03-09 00:00:00 Stop Loss: 1672.0843278027626
Exit: 2188.633257524744 on 2022-04-19 00:00:00 exited on stop loss
Profit: 482.28328193880634
Entry: 2395.300048828125 on 2022-04-26 00:00:00 Stop Loss: 2417.7619474063063
Exit: 2389.0 on 2022-04-29 00:00:00 exited on stop loss
Profit: 475.98323311068134
Entry: 2219.5500488281

7 12 5 5 1.994846077291009
Entry: 1786.0999755859375 on 2022-02-10 00:00:00 Stop Loss: 1750.4700302864658
Exit: 1736.300048828125 on 2022-02-14 00:00:00 exited on stop loss
Profit: -49.7999267578125
Entry: 1656.550048828125 on 2022-03-09 00:00:00 Stop Loss: 1623.5044251607148
Exit: 2179.800048828125 on 2022-04-18 00:00:00 exited on stop loss
Profit: 473.4500732421875
Entry: 2395.300048828125 on 2022-04-26 00:00:00 Stop Loss: 2347.5174997647277
Exit: 2347.5174997647277 on 2022-04-29 00:00:00 exited on stop loss
Profit: 425.66752417879025
Entry: 2219.550048828125 on 2022-05-20 00:00:00 Stop Loss: 2175.2734417455663
Exit: 2168.0 on 2022-05-25 00:00:00 exited on stop loss
Profit: 374.11747535066525
Entry: 2165.64990234375 on 2022-05-30 00:00:00 Stop Loss: 2122.448520218989
Exit: 2122.448520218989 on 2022-06-13 00:00:00 exited on stop loss
Profit: 330.9160932259042
Entry: 2161.449951171875 on 2022-06-24 00:00:00 Stop Loss: 2118.3323516083146
Exit: 2970.193101650422 on 2022-08-23 00:00:00 ex

Exit: 2171.737415780998 on 2022-06-13 00:00:00 exited on stop loss
Profit: 372.13744019506066
Entry: 2161.449951171875 on 2022-06-24 00:00:00 Stop Loss: 2167.5256587954655
Exit: 2557.5689252126226 on 2022-07-28 00:00:00 exited on stop loss
Profit: 768.2564142358083
Entry: 2660.14990234375 on 2022-08-01 00:00:00 Stop Loss: 2667.627425953677
Exit: 3032.64990234375 on 2022-08-23 00:00:00 exited on stop loss
Profit: 1140.7564142358083
Entry: 3355.800048828125 on 2022-09-02 00:00:00 Stop Loss: 3365.2330037428833
Exit: 3460.901069554238 on 2022-09-09 00:00:00 exited on stop loss
Profit: 1245.8574349619212
Entry: 3748.699951171875 on 2022-09-15 00:00:00 Stop Loss: 3759.2373244103997
Exit: 3759.2373244103997 on 2022-09-21 00:00:00 exited on stop loss
Profit: 1256.3948082004458
Entry: 3223.64990234375 on 2022-10-12 00:00:00 Stop Loss: 3232.711391034172
Exit: 3967.721865876604 on 2022-11-16 00:00:00 exited on stop loss
Profit: 2000.4667717333
Entry: 4031.800048828125 on 2022-12-06 00:00:00 Stop 

4 6 7 17 -0.9238182396154647
Entry: 1746.9000244140625 on 2022-02-01 00:00:00 Stop Loss: 1763.0382054674467
Exit: 1739.4000244140625 on 2022-02-08 00:00:00 exited on stop loss
Profit: -7.5
Entry: 1783.1500244140625 on 2022-02-09 00:00:00 Stop Loss: 1799.6230895793071
Exit: 1736.300048828125 on 2022-02-14 00:00:00 exited on stop loss
Profit: -54.3499755859375
Entry: 1730.949951171875 on 2022-02-17 00:00:00 Stop Loss: 1746.9407825394157
Exit: 1738.800048828125 on 2022-02-21 00:00:00 exited on stop loss
Profit: -46.4998779296875
Entry: 1641.800048828125 on 2022-03-02 00:00:00 Stop Loss: 1656.967297137215
Exit: 1590.0 on 2022-03-07 00:00:00 exited on stop loss
Profit: -98.2999267578125
Entry: 1601.5999755859375 on 2022-03-08 00:00:00 Stop Loss: 1616.3958482860771
Exit: 2118.4414560378564 on 2022-04-07 00:00:00 exited on stop loss
Profit: 418.54155369410637
Entry: 2395.300048828125 on 2022-04-26 00:00:00 Stop Loss: 2417.4282675727172
Exit: 2389.0 on 2022-04-29 00:00:00 exited on stop loss
P

...

Entry: 2495.5 on 2022-07-21 00:00:00 Stop Loss: 2520.281824309589
Exit: 2560.0 on 2022-07-27 00:00:00 exited on stop loss
Profit: 907.8855180878247
Entry: 2660.14990234375 on 2022-08-01 00:00:00 Stop Loss: 2686.566799765931
Exit: 2725.196645400009 on 2022-08-05 00:00:00 exited on stop loss
Profit: 972.9322611440837
Entry: 2791.89990234375 on 2022-08-08 00:00:00 Stop Loss: 2819.6251569499777
Exit: 3081.9043322718544 on 2022-08-22 00:00:00 exited on stop loss
Profit: 1262.936691072188
Entry: 3194.35009765625 on 2022-08-30 00:00:00 Stop Loss: 3226.071926108839
Exit: 3497.187747657736 on 2022-09-08 00:00:00 exited on stop loss
Profit: 1565.7743410736741
Entry: 3555.800048828125 on 2022-09-13 00:00:00 Stop Loss: 3591.111293905298
Exit: 3676.2484932040097 on 2022-09-21 00:00:00 exited on stop loss
Profit: 1686.2227854495588
Entry: 3277.60009765625 on 2022-10-07 00:00:00 Stop Loss: 3310.148648959479
Exit: 4040.0 on 2022-11-11 00:00:00 exited on stop loss
Profit: 2448.6226877933086
Entry: 3915

Entry: 3555.800048828125 on 2022-09-13 00:00:00 Stop Loss: 3591.111293905298
Exit: 3676.2484932040097 on 2022-09-21 00:00:00 exited on stop loss
Profit: 1686.2227854495588
Entry: 3277.60009765625 on 2022-10-07 00:00:00 Stop Loss: 3310.148648959479
Exit: 4040.0 on 2022-11-11 00:00:00 exited on stop loss
Profit: 2448.6226877933086
Entry: 3915.10009765625 on 2022-12-01 00:00:00 Stop Loss: 3953.9794095274465
Exit: 4036.49069062761 on 2022-12-09 00:00:00 exited on stop loss
Profit: 2570.0132807646687
Entry: 4016.699951171875 on 2022-12-12 00:00:00 Stop Loss: 4056.588211037343
Exit: 4055.800048828125 on 2022-12-15 00:00:00 exited on stop loss
Profit: 2609.1133784209187
Entry: 4075.300048828125 on 2022-12-19 00:00:00 Stop Loss: 4115.770243105391
Exit: 4115.770243105391 on 2022-12-21 00:00:00 exited on stop loss
Profit: 2649.583572698185
Entry: 3797.699951171875 on 2022-12-28 00:00:00 Stop Loss: 3835.4134085834057
2 6 7 14 -0.9930604812498026
Entry: 1746.9000244140625 on 2022-02-01 00:00:00 St

Entry: 1746.9000244140625 on 2022-02-01 00:00:00 Stop Loss: 1764.2477982034618
Exit: 1764.2477982034618 on 2022-02-07 00:00:00 exited on stop loss
Profit: 17.347773789399298
Entry: 1783.1500244140625 on 2022-02-09 00:00:00 Stop Loss: 1800.8577826279147
Exit: 1736.300048828125 on 2022-02-14 00:00:00 exited on stop loss
Profit: -29.502201796538202
Entry: 1738.0999755859375 on 2022-02-16 00:00:00 Stop Loss: 1755.3603595680938
Exit: 1738.800048828125 on 2022-02-21 00:00:00 exited on stop loss
Profit: -28.802128554350702
Entry: 1644.449951171875 on 2022-02-28 00:00:00 Stop Loss: 1660.7803337708945
Exit: 1590.0 on 2022-03-07 00:00:00 exited on stop loss
Profit: -83.2520797262257
Entry: 1601.5999755859375 on 2022-03-08 00:00:00 Stop Loss: 1617.504832011188
Exit: 1718.295955684493 on 2022-03-15 00:00:00 exited on stop loss
Profit: 33.443900372329836
Entry: 1758.0 on 2022-03-16 00:00:00 Stop Loss: 1775.4580032603715
Exit: 1828.984325315434 on 2022-03-23 00:00:00 exited on stop loss
Profit: 104.

Entry: 1738.0999755859375 on 2022-02-16 00:00:00 Stop Loss: 1755.3603595680938
Exit: 1738.800048828125 on 2022-02-21 00:00:00 exited on stop loss
Profit: -28.802128554350702
Entry: 1644.449951171875 on 2022-02-28 00:00:00 Stop Loss: 1660.7803337708945
Exit: 1590.0 on 2022-03-07 00:00:00 exited on stop loss
Profit: -83.2520797262257
Entry: 1601.5999755859375 on 2022-03-08 00:00:00 Stop Loss: 1617.504832011188
Exit: 1718.295955684493 on 2022-03-15 00:00:00 exited on stop loss
Profit: 33.443900372329836
Entry: 1758.0 on 2022-03-16 00:00:00 Stop Loss: 1775.4580032603715
Exit: 1828.984325315434 on 2022-03-23 00:00:00 exited on stop loss
Profit: 104.42822568776387
Entry: 1867.0 on 2022-03-25 00:00:00 Stop Loss: 1885.5404391849338
Exit: 2119.894885344692 on 2022-04-07 00:00:00 exited on stop loss
Profit: 357.3231110324557
Entry: 2286.35009765625 on 2022-04-21 00:00:00 Stop Loss: 2309.0549369390906
Exit: 2357.2791233188873 on 2022-04-27 00:00:00 exited on stop loss
Profit: 428.252136695093
Ent

Profit: 357.3231110324557
Entry: 2286.35009765625 on 2022-04-21 00:00:00 Stop Loss: 2309.0549369390906
Exit: 2357.2791233188873 on 2022-04-27 00:00:00 exited on stop loss
Profit: 428.252136695093
Entry: 2378.550048828125 on 2022-04-28 00:00:00 Stop Loss: 2402.170489389785
Exit: 2389.0 on 2022-04-29 00:00:00 exited on stop loss
Profit: 438.702087866968
Entry: 2105.89990234375 on 2022-05-16 00:00:00 Stop Loss: 2126.812762048604
Exit: 2126.812762048604 on 2022-05-25 00:00:00 exited on stop loss
Profit: 459.61494757182186
Entry: 2165.64990234375 on 2022-05-30 00:00:00 Stop Loss: 2187.1561156861508
Exit: 2198.820863484753 on 2022-06-08 00:00:00 exited on stop loss
Profit: 492.7859087128247
Entry: 2184.60009765625 on 2022-06-15 00:00:00 Stop Loss: 2206.2944978994187
Exit: 2205.0 on 2022-06-16 00:00:00 exited on stop loss
Profit: 513.1858110565747
Entry: 2161.800048828125 on 2022-06-21 00:00:00 Stop Loss: 2183.268030796676
Exit: 2149.949951171875 on 2022-06-22 00:00:00 exited on stop loss
Pro

In [107]:
test_data = yf.download("adanient.NS",start='2023-01-01',end='2024-01-08')

[*********************100%%**********************]  1 of 1 completed


In [108]:
#Use the best parameters obtained from the GA
#"Best Parameters (Fast Period, Slow Period, ROC Period, RSI Period, ROC Threshold, RSI Derivative Threshold, Stop Loss %):"
#best_parameters = [2, 15, 6, 10, 0] #dlf 2year
best_parameters =[2, 6, 3, 13, -0.9930604812498026]# dlf 1year
# best_parameters = [4, 18, 9, 14, 0]# 1 nifty 1year
# best_parameters = [2, 4, 5, 7, 0]# 2 nifty 1year



# Apply the strategy on out-of-sample data using the best parameters
out_of_sample_profit = evaluate_strategy(test_data.copy(), *best_parameters)


# Print or analyze the performance metrics
print("Out-of-sample profit:", out_of_sample_profit)

2 6 3 13 -0.9930604812498026
Entry: 3442.0 on 2023-01-24 00:00:00 Stop Loss: 3476.181141764618
Exit: 3422.0 on 2023-01-25 00:00:00 exited on stop loss
Profit: -20.0
Entry: 1802.949951171875 on 2023-02-07 00:00:00 Stop Loss: 1820.8543346336755
Exit: 1535.0 on 2023-02-22 00:00:00 exited on stop loss
Profit: -287.949951171875
Entry: 1363.8499755859375 on 2023-02-28 00:00:00 Stop Loss: 1377.3938307170165
Exit: 1870.0 on 2023-03-10 00:00:00 exited on stop loss
Profit: 218.2000732421875
Entry: 1740.4000244140625 on 2023-03-29 00:00:00 Stop Loss: 1757.6832492721805
Exit: 1869.3310036646753 on 2023-04-18 00:00:00 exited on stop loss
Profit: 347.13105249280034
Entry: 1847.9000244140625 on 2023-04-26 00:00:00 Stop Loss: 1866.250789289524
Exit: 1866.250789289524 on 2023-05-03 00:00:00 exited on stop loss
Profit: 365.4818173682618
Entry: 1911.25 on 2023-05-04 00:00:00 Stop Loss: 1930.229868447887
Exit: 1920.300048828125 on 2023-05-08 00:00:00 exited on stop loss
Profit: 374.5318661963868
Entry: 19

In [1]:
140/632

0.22151898734177214